In [ ]:
import numpy as np
import pandas as pd
import folium
import openrouteservice as ors
ORSkey = '5b3ce3597851110001cf624891902f8f5f1743e39ce3678f063f2d27'

In [ ]:
locations = pd.read_csv("WoolworthsLocations.csv")
coords = locations[['Long', 'Lat']] # Mapping packages work with Long, Lat arrays
coords = coords.to_numpy().tolist() # Make the arrays into a list of lists.
# Folium, however, requires Lat, Long arrays - so a reversal is needed.
# coords[0] is the warehouse
m = folium.Map(location = list(reversed(coords[2])), zoom_start=10)
folium.Marker(list(reversed(coords[0])), popup = locations.Store[0], icon = folium.Icon(color = 'black')).add_to(m)
for i in range(1, len(coords)):
    if locations.Type[i] == "Countdown":
        iconCol = "green"
    elif locations.Type[i] == "FreshChoice":
        iconCol = "blue"
    elif locations.Type[i] == "SuperValue":
        iconCol = "red"
    elif locations.Type[i] == "Countdown Metro":
        iconCol = "orange"
    elif locations.Type[i] == "Distribution Centre":
        iconCol = "black"
    folium.Marker(list(reversed(coords[i])), popup = locations.Store[i], icon = folium.Icon(color = iconCol)).add_to(m)

m

In [ ]:
# plotting routes
# Boot up client to OpenRouteService. ORSkey is your own key as a string.
client = ors.Client(key=ORSkey)
route = client.directions(
    coordinates = [coords[55], coords[21]], # Distribution Centre to Countdown Mangere East
    # We can have more than two coords - it will generate a path between those coords in order.
    profile = 'driving-hgv', # can be driving-car, driving-hgv, etc.
    format='geojson',
    validate = False
    )

# get distance in meters
print(route['features'][0]['properties']['summary']['distance'])

# Get duration in seconds
print(route['features'][0]['properties']['summary']['duration'])

m = folium.Map(location = [-36.95770671222872, 174.81407132219618], zoom_start=15)
folium.PolyLine(locations = [list(reversed(coord))
for coord in
route['features'][0]['geometry']['coordinates']]).add_to(m)

m

4351.9
428.1


In [ ]:

matrix = client.distance_matrix(
    locations=coords,
    sources = list(range(50, 66)), # sequence numbers for sources/dests of interest
    destinations = list(range(0, 50)),
    profile='driving-hgv',
    metrics=['distance', 'duration'],
    validate=False,
)

pd.DataFrame(matrix['distances']).to_csv('distances.csv')
pd.DataFrame(matrix['distances']).to_csv('distances.csv')

In [ ]:
# plotting Monday routes
# Boot up client to OpenRouteService. ORSkey is your own key as a string.
client = ors.Client(key=ORSkey)

sol = [[["Distribution Centre Auckland", "Countdown Northcote", "Countdown Takapuna", "Countdown Hauraki Corner"], ["Distribution Centre Auckland", "Countdown Milford", "Countdown Mairangi Bay", "Countdown Browns Bay"], ["Distribution Centre Auckland", "Countdown Birkenhead", "Countdown Glenfield", "Countdown Sunnynook"]],[["Distribution Centre Auckland", "Countdown Te Atatu", "Countdown Te Atatu South", "Countdown Lincoln Road"], ["Distribution Centre Auckland", "Countdown Hobsonville", "Countdown Northwest", "Countdown Westgate"], ["Distribution Centre Auckland", "Countdown Henderson", "SuperValue Palomino", "FreshChoice Ranui"]],[["Distribution Centre Auckland", "Countdown Manurewa", "Countdown Takanini"], ["Distribution Centre Auckland", "Countdown Papakura", "Countdown Roselands", "SuperValue Papakura"], ["Distribution Centre Auckland", "Countdown Manukau", "Countdown Manukau Mall", "SuperValue Flatbush"]],[["Distribution Centre Auckland", "Countdown Auckland City", "Countdown Victoria Street West", "Countdown Mt Eden"], ["Distribution Centre Auckland", "Countdown Airport", "Countdown Mangere Mall", "Countdown Mangere East"], ["Distribution Centre Auckland", "Countdown Mt Roskill", "Countdown St Lukes", "Countdown Three Kings"], ["Distribution Centre Auckland", "Countdown Aviemore Drive", "Countdown Highland Park", "Countdown Meadowlands"], ["Distribution Centre Auckland", "Countdown Mt Wellington", "Countdown Sylvia Park", "FreshChoice Otahuhu"], ["Distribution Centre Auckland", "Countdown Grey Lynn Central", "Countdown Ponsonby", "Countdown Pt Chevalier"], ["Distribution Centre Auckland", "Countdown Botany Downs", "Countdown Howick", "FreshChoice Half Moon Bay"], ["Distribution Centre Auckland", "Countdown Greenlane", "Countdown Meadowbank", "Countdown Onehunga"], ["Distribution Centre Auckland", "Countdown Pakuranga", "Countdown St Johns", "Countdown Papatoetoe"], ["Distribution Centre Auckland", "Countdown Blockhouse Bay", "Countdown Lynfield", "FreshChoice Mangere Bridge"], ["Distribution Centre Auckland", "Countdown Grey Lynn", "Countdown Metro Halsey Street", "Countdown Metro Albert Street", "Countdown Newmarket"], ["Distribution Centre Auckland", "Countdown Kelston", "FreshChoice Glen Eden", "SuperValue Titirangi", "Countdown Lynmall", "SuperValue Avondale"]]]
solLoc = sol.copy()
        
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        
        solLoc[i][j] += ["Distribution Centre Auckland"]
        
        for z in range(len(solLoc[i][j])): # looking into each locations within a route
            for x in range(66):
                if solLoc[i][j][z] == locations.Store[x]:
                    solLoc[i][j][z] = coords[x]

list_colors = ["#201923"
,"#ffffff"
,"#fcff5d"
,"#7dfc00"
,"#0ec434"
,"#228c68"
,"#8ad8e8"
,"#235b54"
,"#29bdab"
,"#3998f5"
,"#37294f"
,"#277da7"
,"#3750db"
,"#f22020"
,"#991919"
,"#ff95c4"
,"#e68f66"
,"#c56133"
,"#96341c"
,"#632819"
,"#ffc413"
,"#f47a22"
,"#2f2aa0"
,"#b732cc"
,"#772b9d"
,"#f07cab"
,"#d30b94"
,"#edeff3"
,"#c3a5b4"
,"#946aa2"
,"#5d4c86"]

m = folium.Map(location = [-36.95770671222872, 174.81407132219618], zoom_start=10)
x = 0
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        route = client.directions(
            coordinates = solLoc[i][j], # Distribution Centre to Countdown Mangere East
            # We can have more than two coords - it will generate a path between those coords in order.
            profile = 'driving-hgv', # can be driving-car, driving-hgv, etc.
            format='geojson',
            validate = False
            )

        folium.PolyLine(locations = [list(reversed(coord))
        for coord in
        route['features'][0]['geometry']['coordinates']], color = list_colors[x%len(list_colors)]).add_to(m)
        
        x+=1

# print the cost of the route
totalCost = 0
rCost = [[1032.4461111111113, 1202.0248611111112, 1133.8149305555555],[1000.2772222222223, 1062.1827777777778, 854.611875],[1004.3464583333333, 778.1818750000001, 914.6437500000001, 967.8486111111113, 843.455625, 973.0285416666668, 902.3283333333335, 948.9278472222223, 1019.3179166666669, 825.635625, 1001.6697916666667, 1029.3477777777778],[647.068125, 826.931875, 789.1481249999999]]
for i in range(len(rCost)):
    for j in range(len(rCost[i])):
        totalCost += rCost[i][j]
print("Monday total cost : $%.2f" % (totalCost))

# print the duration of the route 
totalDuration = 0
rDuration = [[4.481622222222223, 5.0982722222222225, 4.850236111111111],[4.364644444444445, 4.589755555555556, 3.7982750000000003],[4.379441666666667, 3.4585861111111114, 4.05325, 4.246722222222223, 3.7486916666666668, 4.265558333333334, 4.008466666666667, 4.177919444444445, 4.433883333333334, 3.6694916666666666, 4.3697083333333335, 4.470355555555556],[2.8758583333333334, 3.6752527777777777, 3.507325]]
for i in range(len(rDuration)):
    for j in range(len(rDuration[i])):
        totalDuration += rDuration[i][j]
print("Monday total duration : %.2f hours" % (totalDuration))

m


Monday total cost : $19757.24
Monday total duration : 86.52 hours


In [ ]:
# plotting Tuesday routes
# Boot up client to OpenRouteService. ORSkey is your own key as a string.
client = ors.Client(key=ORSkey)

sol = [[["Distribution Centre Auckland", "Countdown Takapuna", "Countdown Hauraki Corner", "Countdown Milford"], ["Distribution Centre Auckland", "Countdown Birkenhead", "Countdown Northcote", "Countdown Glenfield"], ["Distribution Centre Auckland", "Countdown Sunnynook", "Countdown Mairangi Bay", "Countdown Browns Bay"]],[["Distribution Centre Auckland", "Countdown Te Atatu South", "Countdown Henderson", "SuperValue Palomino"], ["Distribution Centre Auckland", "Countdown Westgate", "Countdown Lincoln Road", "FreshChoice Ranui"], ["Distribution Centre Auckland", "Countdown Hobsonville", "Countdown Northwest", "Countdown Te Atatu"]],[["Distribution Centre Auckland", "Countdown Manukau Mall", "Countdown Manukau"], ["Distribution Centre Auckland", "Countdown Papakura", "Countdown Roselands", "SuperValue Papakura"], ["Distribution Centre Auckland", "Countdown Manurewa", "Countdown Takanini", "SuperValue Flatbush"]],[["Distribution Centre Auckland", "Countdown Papatoetoe", "Countdown Meadowlands"], ["Distribution Centre Auckland", "Countdown Mt Roskill", "Countdown St Lukes", "Countdown Pt Chevalier"], ["Distribution Centre Auckland", "Countdown Grey Lynn", "Countdown Grey Lynn Central", "Countdown Ponsonby"], ["Distribution Centre Auckland", "Countdown Blockhouse Bay", "Countdown Lynfield", "Countdown Lynmall"], ["Distribution Centre Auckland", "Countdown Mt Eden", "Countdown Newmarket", "Countdown Three Kings"], ["Distribution Centre Auckland", "Countdown Aviemore Drive", "Countdown Highland Park", "Countdown Pakuranga"], ["Distribution Centre Auckland", "Countdown Botany Downs", "Countdown Howick", "FreshChoice Half Moon Bay"], ["Distribution Centre Auckland", "Countdown Greenlane", "Countdown Meadowbank", "Countdown St Johns"], ["Distribution Centre Auckland", "Countdown Auckland City", "Countdown Metro Albert Street", "Countdown Metro Halsey Street", "Countdown Victoria Street West"], ["Distribution Centre Auckland", "Countdown Kelston", "FreshChoice Glen Eden", "SuperValue Titirangi", "SuperValue Avondale"], ["Distribution Centre Auckland", "Countdown Onehunga", "Countdown Mt Wellington", "Countdown Sylvia Park", "FreshChoice Otahuhu"], ["Distribution Centre Auckland", "FreshChoice Mangere Bridge", "Countdown Airport", "Countdown Mangere Mall", "Countdown Mangere East"]]]
solLoc = sol.copy()
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        
        solLoc[i][j] += ["Distribution Centre Auckland"]
        
        for z in range(len(solLoc[i][j])): # looking into each locations within a route
            for x in range(66):
                if solLoc[i][j][z] == locations.Store[x]:
                    solLoc[i][j][z] = coords[x]

list_colors = ["#201923"
,"#ffffff"
,"#fcff5d"
,"#7dfc00"
,"#0ec434"
,"#228c68"
,"#8ad8e8"
,"#235b54"
,"#29bdab"
,"#3998f5"
,"#37294f"
,"#277da7"
,"#3750db"
,"#f22020"
,"#991919"
,"#ff95c4"
,"#e68f66"
,"#c56133"
,"#96341c"
,"#632819"
,"#ffc413"
,"#f47a22"
,"#2f2aa0"
,"#b732cc"
,"#772b9d"
,"#f07cab"
,"#d30b94"
,"#edeff3"
,"#c3a5b4"
,"#946aa2"
,"#5d4c86"]

m = folium.Map(location = [-36.95770671222872, 174.81407132219618], zoom_start=10)
x = 0
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        route = client.directions(
            coordinates = solLoc[i][j], # Distribution Centre to Countdown Mangere East
            # We can have more than two coords - it will generate a path between those coords in order.
            profile = 'driving-hgv', # can be driving-car, driving-hgv, etc.
            format='geojson',
            validate = False
            )

        folium.PolyLine(locations = [list(reversed(coord))
        for coord in
        route['features'][0]['geometry']['coordinates']], color = list_colors[x%len(list_colors)]).add_to(m)
        
        x+=1

# print the cost of the route
totalCost = 0
rCost = [[1011.9272916666667, 920.7678472222223, 1115.9536805555554],[885.7950000000001, 1050.6213194444447, 1109.303263888889],[866.5381249999999, 922.9854166666667, 899.6775000000001, 914.0143055555557, 907.8497222222221, 953.4653472222224, 971.0783333333335, 892.11625, 1021.6928472222223, 989.106875, 894.2843750000001, 879.2181250000001],[713.6712500000001, 883.181875, 925.6047916666666]]
for i in range(len(rCost)):
    for j in range(len(rCost[i])):
        totalCost += rCost[i][j]
print("Tuesday total cost : $%.2f" % (totalCost))

# print the duration of the route 
totalDuration = 0
rDuration = [[4.407008333333334, 4.075519444444445, 4.785286111111111],[3.936866666666667, 4.5477138888888895, 4.761102777777778],[3.8512805555555554, 4.083583333333333, 3.998566666666667, 4.0509611111111115, 4.028544444444444, 4.194419444444445, 4.258466666666667, 3.964961111111111, 4.442519444444445, 4.324025, 3.9745972222222226, 3.9076361111111115],[3.1718722222222224, 3.9252527777777777, 4.093108333333333]]
for i in range(len(rDuration)):
    for j in range(len(rDuration[i])):
        totalDuration += rDuration[i][j]
print("Tuesday total duration : %.2f hours" % (totalDuration))

m

Tuesday total cost : $19728.85
Tuesday total duration : 86.78 hours


In [ ]:
# plotting Wednesday routes
# Boot up client to OpenRouteService. ORSkey is your own key as a string.
client = ors.Client(key=ORSkey)

sol = [[["Distribution Centre Auckland", "Countdown Northcote", "Countdown Glenfield", "Countdown Sunnynook"], ["Distribution Centre Auckland", "Countdown Birkenhead", "Countdown Takapuna", "Countdown Hauraki Corner"], ["Distribution Centre Auckland", "Countdown Milford", "Countdown Mairangi Bay", "Countdown Browns Bay"]],[["Distribution Centre Auckland", "Countdown Te Atatu South", "Countdown Te Atatu"], ["Distribution Centre Auckland", "Countdown Hobsonville", "Countdown Northwest", "Countdown Westgate"], ["Distribution Centre Auckland", "Countdown Lincoln Road", "FreshChoice Ranui", "SuperValue Palomino", "Countdown Henderson"]],[["Distribution Centre Auckland", "Countdown Manurewa", "Countdown Takanini"], ["Distribution Centre Auckland", "Countdown Papakura", "Countdown Roselands", "SuperValue Papakura"], ["Distribution Centre Auckland", "Countdown Manukau", "Countdown Manukau Mall", "SuperValue Flatbush"]],[["Distribution Centre Auckland", "Countdown Ponsonby", "Countdown Grey Lynn"], ["Distribution Centre Auckland", "Countdown Botany Downs", "Countdown Meadowlands", "Countdown Howick"], ["Distribution Centre Auckland", "Countdown Airport", "Countdown Mangere Mall", "Countdown Mangere East"], ["Distribution Centre Auckland", "Countdown Meadowbank", "Countdown St Johns", "Countdown Pakuranga"], ["Distribution Centre Auckland", "Countdown Mt Wellington", "Countdown Sylvia Park", "Countdown Papatoetoe"], ["Distribution Centre Auckland", "Countdown Grey Lynn Central", "Countdown Pt Chevalier", "Countdown Mt Roskill"], ["Distribution Centre Auckland", "Countdown Mt Eden", "Countdown St Lukes", "Countdown Three Kings"], ["Distribution Centre Auckland", "Countdown Greenlane", "Countdown Newmarket", "Countdown Onehunga"], ["Distribution Centre Auckland", "Countdown Auckland City", "Countdown Metro Albert Street", "Countdown Metro Halsey Street", "Countdown Victoria Street West"], ["Distribution Centre Auckland", "Countdown Blockhouse Bay", "SuperValue Titirangi", "FreshChoice Glen Eden", "Countdown Kelston"], ["Distribution Centre Auckland", "Countdown Lynfield", "SuperValue Avondale", "Countdown Lynmall", "FreshChoice Mangere Bridge"], ["Distribution Centre Auckland", "Countdown Aviemore Drive", "Countdown Highland Park", "FreshChoice Half Moon Bay", "FreshChoice Otahuhu"]]]
solLoc = sol.copy()
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        solLoc[i][j] += ["Distribution Centre Auckland"]
        for z in range(len(solLoc[i][j])): # looking into each locations within a route
            for x in range(66):
                if solLoc[i][j][z] == locations.Store[x]:
                    solLoc[i][j][z] = coords[x]

list_colors = ["#201923"
,"#ffffff"
,"#fcff5d"
,"#7dfc00"
,"#0ec434"
,"#228c68"
,"#8ad8e8"
,"#235b54"
,"#29bdab"
,"#3998f5"
,"#37294f"
,"#277da7"
,"#3750db"
,"#f22020"
,"#991919"
,"#ff95c4"
,"#e68f66"
,"#c56133"
,"#96341c"
,"#632819"
,"#ffc413"
,"#f47a22"
,"#2f2aa0"
,"#b732cc"
,"#772b9d"
,"#f07cab"
,"#d30b94"
,"#edeff3"
,"#c3a5b4"
,"#946aa2"
,"#5d4c86"]

m = folium.Map(location = [-36.95770671222872, 174.81407132219618], zoom_start=10)
x = 0
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        route = client.directions(
            coordinates = solLoc[i][j], # Distribution Centre to Countdown Mangere East
            # We can have more than two coords - it will generate a path between those coords in order.
            profile = 'driving-hgv', # can be driving-car, driving-hgv, etc.
            format='geojson',
            validate = False
            )

        folium.PolyLine(locations = [list(reversed(coord))
        for coord in
        route['features'][0]['geometry']['coordinates']], color = list_colors[x%len(list_colors)]).add_to(m)
        
        x+=1

# print the cost of the route
totalCost = 0
rCost = [[1094.8886805555555, 1087.4331250000002, 1202.0248611111112],[645.41625, 1062.1827777777778, 1019.4409027777778],[777.5781249999999, 1014.2021527777778, 778.1818750000001, 877.9675, 881.261875, 937.0715277777778, 933.4797222222222, 955.0580555555557, 1021.6928472222223, 978.1618750000001, 917.524375, 934.2917361111114],[703.318125, 913.8195138888889, 789.1481249999999]]
for i in range(len(rCost)):
    for j in range(len(rCost[i])):
        totalCost += rCost[i][j]
print("Wednesday total cost : $%.2f" % (totalCost))

# print the duration of the route 
totalDuration = 0
rDuration = [[4.708686111111112, 4.6815750000000005, 5.0982722222222225],[2.8685166666666664, 4.589755555555556, 4.434330555555555],[3.4559027777777773, 4.415280555555555, 3.4585861111111114, 3.9020777777777775, 3.9167194444444444, 4.134805555555555, 4.121744444444444, 4.200211111111112, 4.442519444444445, 4.284225, 4.063725, 4.124697222222223],[3.1258583333333334, 4.050252777777778, 3.507325]]
for i in range(len(rDuration)):
    for j in range(len(rDuration[i])):
        totalDuration += rDuration[i][j]
print("Wednesday total duration : %.2f hours" % (totalDuration))

m

Wednesday total cost : $19524.14
Wednesday total duration : 85.59 hours


In [ ]:
# plotting Thursday routes
# Boot up client to OpenRouteService. ORSkey is your own key as a string.
client = ors.Client(key=ORSkey)

sol = [[["Distribution Centre Auckland", "Countdown Birkenhead", "Countdown Northcote", "Countdown Takapuna"], ["Distribution Centre Auckland", "Countdown Hauraki Corner", "Countdown Milford", "Countdown Sunnynook"], ["Distribution Centre Auckland", "Countdown Glenfield", "Countdown Mairangi Bay", "Countdown Browns Bay"]],[["Distribution Centre Auckland", "Countdown Te Atatu", "Countdown Te Atatu South", "Countdown Lincoln Road"], ["Distribution Centre Auckland", "Countdown Hobsonville", "Countdown Northwest", "Countdown Westgate"], ["Distribution Centre Auckland", "Countdown Henderson", "SuperValue Palomino", "FreshChoice Ranui"]],[["Distribution Centre Auckland", "Countdown Manurewa", "Countdown Takanini"], ["Distribution Centre Auckland", "Countdown Papakura", "Countdown Roselands", "SuperValue Papakura"], ["Distribution Centre Auckland", "Countdown Manukau", "Countdown Manukau Mall", "SuperValue Flatbush"]],[["Distribution Centre Auckland", "Countdown Onehunga", "Countdown Three Kings"], ["Distribution Centre Auckland", "Countdown Mangere East", "Countdown Papatoetoe"], ["Distribution Centre Auckland", "Countdown Auckland City", "Countdown Newmarket", "Countdown Greenlane"], ["Distribution Centre Auckland", "Countdown Mt Roskill", "Countdown St Lukes", "Countdown Pt Chevalier"], ["Distribution Centre Auckland", "Countdown Grey Lynn Central", "Countdown Ponsonby", "Countdown Mt Eden"], ["Distribution Centre Auckland", "Countdown Meadowbank", "Countdown St Johns", "Countdown Pakuranga"], ["Distribution Centre Auckland", "Countdown Aviemore Drive", "Countdown Highland Park", "Countdown Meadowlands"], ["Distribution Centre Auckland", "Countdown Blockhouse Bay", "Countdown Lynfield", "SuperValue Avondale"], ["Distribution Centre Auckland", "Countdown Mt Wellington", "Countdown Sylvia Park", "FreshChoice Otahuhu"], ["Distribution Centre Auckland", "Countdown Botany Downs", "Countdown Howick", "FreshChoice Half Moon Bay"], ["Distribution Centre Auckland", "FreshChoice Mangere Bridge", "Countdown Airport", "Countdown Mangere Mall"], ["Distribution Centre Auckland", "Countdown Grey Lynn", "Countdown Metro Halsey Street", "Countdown Metro Albert Street", "Countdown Victoria Street West"], ["Distribution Centre Auckland", "Countdown Kelston", "FreshChoice Glen Eden", "SuperValue Titirangi", "Countdown Lynmall"]]]
solLoc = sol.copy()
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        solLoc[i][j] += ["Distribution Centre Auckland"]
        for z in range(len(solLoc[i][j])): # looking into each locations within a route
            for x in range(66):
                if solLoc[i][j][z] == locations.Store[x]:
                    solLoc[i][j][z] = coords[x]

list_colors = ["#201923"
,"#ffffff"
,"#fcff5d"
,"#7dfc00"
,"#0ec434"
,"#228c68"
,"#8ad8e8"
,"#235b54"
,"#29bdab"
,"#3998f5"
,"#37294f"
,"#277da7"
,"#3750db"
,"#f22020"
,"#991919"
,"#ff95c4"
,"#e68f66"
,"#c56133"
,"#96341c"
,"#632819"
,"#ffc413"
,"#f47a22"
,"#2f2aa0"
,"#b732cc"
,"#772b9d"
,"#f07cab"
,"#d30b94"
,"#edeff3"
,"#c3a5b4"
,"#946aa2"
,"#5d4c86"]

m = folium.Map(location = [-36.95770671222872, 174.81407132219618], zoom_start=10)
x = 0
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        route = client.directions(
            coordinates = solLoc[i][j], # Distribution Centre to Countdown Mangere East
            # We can have more than two coords - it will generate a path between those coords in order.
            profile = 'driving-hgv', # can be driving-car, driving-hgv, etc.
            format='geojson',
            validate = False
            )

        folium.PolyLine(locations = [list(reversed(coord))
        for coord in
        route['features'][0]['geometry']['coordinates']], color = list_colors[x%len(list_colors)]).add_to(m)
        
        x+=1

# print the cost of the route
totalCost = 0
rCost = [[1067.112916666667, 964.2430555555555, 1221.5391666666665],[931.5272222222223, 1062.1827777777778, 913.2756250000001],[667.89375, 651.0956249999999, 926.5947916666668, 922.9854166666667, 920.612777777778, 941.8213888888888, 899.2625, 829.8075, 759.080625, 971.0783333333335, 690.320625, 1028.816111111111, 1024.308402777778],[675.193125, 883.181875, 676.6481249999999]]
for i in range(len(rCost)):
    for j in range(len(rCost[i])):
        totalCost += rCost[i][j]
print("Thursday total cost : $%.2f" % (totalCost))

# print the duration of the route 
totalDuration = 0
rDuration = [[4.607683333333334, 4.233611111111111, 5.169233333333333],[4.114644444444445, 4.589755555555556, 4.048275],[2.9684166666666667, 2.893758333333333, 4.096708333333334, 4.083583333333333, 4.074955555555556, 4.1520777777777775, 3.9967222222222225, 3.6880333333333333, 3.3736916666666668, 4.258466666666667, 3.0680916666666667, 4.468422222222221, 4.452030555555556],[3.0008583333333334, 3.9252527777777777, 3.007325]]
for i in range(len(rDuration)):
    for j in range(len(rDuration[i])):
        totalDuration += rDuration[i][j]
print("Thursday total duration : %.2f hours" % (totalDuration))

m

Thursday total cost : $19628.58
Thursday total duration : 86.27 hours


In [ ]:
# plotting Friday routes
# Boot up client to OpenRouteService. ORSkey is your own key as a string.
client = ors.Client(key=ORSkey)

sol = [[["Distribution Centre Auckland", "Countdown Takapuna", "Countdown Hauraki Corner"], ["Distribution Centre Auckland", "Countdown Mairangi Bay", "Countdown Browns Bay"], ["Distribution Centre Auckland", "Countdown Northcote", "Countdown Birkenhead"], ["Distribution Centre Auckland", "Countdown Glenfield", "Countdown Sunnynook", "Countdown Milford"]],[["Distribution Centre Auckland", "Countdown Te Atatu", "Countdown Te Atatu South", "Countdown Lincoln Road"], ["Distribution Centre Auckland", "Countdown Hobsonville", "Countdown Northwest", "Countdown Westgate"], ["Distribution Centre Auckland", "Countdown Henderson", "SuperValue Palomino", "FreshChoice Ranui"]],[["Distribution Centre Auckland", "Countdown Manurewa", "Countdown Takanini"], ["Distribution Centre Auckland", "Countdown Papakura", "Countdown Roselands", "SuperValue Papakura"], ["Distribution Centre Auckland", "Countdown Manukau", "Countdown Manukau Mall", "SuperValue Flatbush"]],[["Distribution Centre Auckland", "Countdown Mangere East"], ["Distribution Centre Auckland", "Countdown Mt Eden", "Countdown Ponsonby"], ["Distribution Centre Auckland", "Countdown Botany Downs", "Countdown Meadowlands", "Countdown Howick"], ["Distribution Centre Auckland", "Countdown Meadowbank", "Countdown St Johns", "Countdown Pakuranga"], ["Distribution Centre Auckland", "Countdown Aviemore Drive", "Countdown Highland Park", "FreshChoice Half Moon Bay"], ["Distribution Centre Auckland", "Countdown Mt Wellington", "Countdown Sylvia Park", "Countdown Papatoetoe"], ["Distribution Centre Auckland", "Countdown Mt Roskill", "Countdown St Lukes", "Countdown Three Kings"], ["Distribution Centre Auckland", "Countdown Grey Lynn", "Countdown Grey Lynn Central", "Countdown Pt Chevalier"], ["Distribution Centre Auckland", "Countdown Onehunga", "Countdown Airport", "Countdown Mangere Mall"], ["Distribution Centre Auckland", "Countdown Greenlane", "Countdown Newmarket", "FreshChoice Otahuhu"], ["Distribution Centre Auckland", "Countdown Auckland City", "Countdown Metro Albert Street", "Countdown Metro Halsey Street", "Countdown Victoria Street West"], ["Distribution Centre Auckland", "Countdown Blockhouse Bay", "SuperValue Titirangi", "FreshChoice Glen Eden", "Countdown Kelston"], ["Distribution Centre Auckland", "Countdown Lynfield", "SuperValue Avondale", "Countdown Lynmall", "FreshChoice Mangere Bridge"]]]
solLoc = sol.copy()
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        solLoc[i][j] += ["Distribution Centre Auckland"]
        for z in range(len(solLoc[i][j])): # looking into each locations within a route
            for x in range(66):
                if solLoc[i][j][z] == locations.Store[x]:
                    solLoc[i][j][z] = coords[x]

list_colors = ["#201923"
,"#ffffff"
,"#fcff5d"
,"#7dfc00"
,"#0ec434"
,"#228c68"
,"#8ad8e8"
,"#235b54"
,"#29bdab"
,"#3998f5"
,"#37294f"
,"#277da7"
,"#3750db"
,"#f22020"
,"#991919"
,"#ff95c4"
,"#e68f66"
,"#c56133"
,"#96341c"
,"#632819"
,"#ffc413"
,"#f47a22"
,"#2f2aa0"
,"#b732cc"
,"#772b9d"
,"#f07cab"
,"#d30b94"
,"#edeff3"
,"#c3a5b4"
,"#946aa2"
,"#5d4c86"]

m = folium.Map(location = [-36.95770671222872, 174.81407132219618], zoom_start=10)
x = 0
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        route = client.directions(
            coordinates = solLoc[i][j], # Distribution Centre to Countdown Mangere East
            # We can have more than two coords - it will generate a path between those coords in order.
            profile = 'driving-hgv', # can be driving-car, driving-hgv, etc.
            format='geojson',
            validate = False
            )

        folium.PolyLine(locations = [list(reversed(coord))
        for coord in
        route['features'][0]['geometry']['coordinates']], color = list_colors[x%len(list_colors)]).add_to(m)
        
        x+=1

# print the cost of the route
totalCost = 0
rCost = [[782.005625, 1011.6056944444445, 856.2575, 1090.731597222222],[1034.6522222222222, 959.0577777777778, 854.611875],[278.86125000000004, 800.2862499999999, 979.8271527777778, 941.8213888888888, 866.2956250000002, 881.261875, 883.85625, 986.7518055555556, 802.880625, 825.2350000000001, 1021.6928472222223, 943.7868750000001, 951.899375],[787.693125, 826.931875, 817.2731249999999]]
for i in range(len(rCost)):
    for j in range(len(rCost[i])):
        totalCost += rCost[i][j]
print("Friday total cost : $%.2f" % (totalCost))

# print the duration of the route 
totalDuration = 0
rDuration = [[3.4755805555555557, 4.405838888888889, 3.805588888888889, 4.693569444444444],[4.489644444444445, 4.214755555555556, 3.7982750000000003],[1.2393833333333335, 3.5568277777777775, 4.290280555555555, 4.1520777777777775, 3.8502027777777785, 3.9167194444444444, 3.9282500000000002, 4.315461111111111, 3.5683583333333333, 3.6677111111111116, 4.442519444444445, 4.159225, 4.188725],[3.5008583333333334, 3.6752527777777777, 3.632325]]
for i in range(len(rDuration)):
    for j in range(len(rDuration[i])):
        totalDuration += rDuration[i][j]
print("Friday total duration : %.2f hours" % (totalDuration))
        
m

Friday total cost : $20185.28
Friday total duration : 88.97 hours


In [ ]:
# plotting Saturday routes
# Boot up client to OpenRouteService. ORSkey is your own key as a string.
client = ors.Client(key=ORSkey)

sol = [[["Distribution Centre Auckland", "Countdown Birkenhead", "Countdown Northcote", "Countdown Takapuna", "Countdown Hauraki Corner"], ["Distribution Centre Auckland", "Countdown Glenfield", "Countdown Sunnynook", "Countdown Mairangi Bay", "Countdown Browns Bay", "Countdown Milford"]],[["Distribution Centre Auckland", "Countdown Hobsonville", "Countdown Northwest", "Countdown Westgate"], ["Distribution Centre Auckland", "Countdown Te Atatu", "Countdown Te Atatu South", "Countdown Lincoln Road", "Countdown Henderson"]],[["Distribution Centre Auckland", "Countdown Manukau Mall", "Countdown Manukau"], ["Distribution Centre Auckland", "Countdown Manurewa", "Countdown Takanini", "Countdown Roselands", "Countdown Papakura"]],[["Distribution Centre Auckland", "Countdown Mangere Mall", "Countdown Airport"], ["Distribution Centre Auckland", "Countdown Greenlane", "Countdown Meadowbank", "Countdown St Johns", "Countdown Pakuranga"], ["Distribution Centre Auckland", "Countdown Aviemore Drive", "Countdown Highland Park", "Countdown Meadowlands", "Countdown Howick", "Countdown Botany Downs"], ["Distribution Centre Auckland", "Countdown Auckland City", "Countdown Victoria Street West", "Countdown Newmarket", "Countdown Mt Eden", "Countdown St Lukes"], ["Distribution Centre Auckland", "Countdown Grey Lynn", "Countdown Grey Lynn Central", "Countdown Ponsonby", "Countdown Pt Chevalier", "Countdown Mt Roskill"], ["Distribution Centre Auckland", "Countdown Onehunga", "Countdown Mt Wellington", "Countdown Sylvia Park", "Countdown Papatoetoe", "Countdown Mangere East"], ["Distribution Centre Auckland", "Countdown Lynmall", "Countdown Kelston", "Countdown Blockhouse Bay", "Countdown Lynfield", "Countdown Three Kings"]]]
solLoc = sol.copy()
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        solLoc[i][j] += ["Distribution Centre Auckland"]
        for z in range(len(solLoc[i][j])): # looking into each locations within a route
            for x in range(66):
                if solLoc[i][j][z] == locations.Store[x]:
                    solLoc[i][j][z] = coords[x]

list_colors = ["#201923"
,"#ffffff"
,"#fcff5d"
,"#7dfc00"
,"#0ec434"
,"#228c68"
,"#8ad8e8"
,"#235b54"
,"#29bdab"
,"#3998f5"
,"#37294f"
,"#277da7"
,"#3750db"
,"#f22020"
,"#991919"
,"#ff95c4"
,"#e68f66"
,"#c56133"
,"#96341c"
,"#632819"
,"#ffc413"
,"#f47a22"
,"#2f2aa0"
,"#b732cc"
,"#772b9d"
,"#f07cab"
,"#d30b94"
,"#edeff3"
,"#c3a5b4"
,"#946aa2"
,"#5d4c86"]

m = folium.Map(location = [-36.95770671222872, 174.81407132219618], zoom_start=10)
x = 0
for i in range(len(sol)): # looking into each region
    for j in range(len(sol[i])): # looking into each route
        route = client.directions(
            coordinates = solLoc[i][j], # Distribution Centre to Countdown Mangere East
            # We can have more than two coords - it will generate a path between those coords in order.
            profile = 'driving-hgv', # can be driving-car, driving-hgv, etc.
            format='geojson',
            validate = False
            )

        folium.PolyLine(locations = [list(reversed(coord))
        for coord in
        route['features'][0]['geometry']['coordinates']], color = list_colors[x%len(list_colors)]).add_to(m)
        
        x+=1

# print the cost of the route
totalCost = 0
rCost = [[868.0637499999999, 1120.5118055555556],[751.445, 828.5625000000001],[373.061875, 760.33125, 795.3575, 858.803125, 918.370763888889, 746.233125, 817.8999999999999],[432.42125000000004, 809.9968749999999]]
for i in range(len(rCost)):
    for j in range(len(rCost[i])):
        totalCost += rCost[i][j]
print("Saturday total cost : $%.2f" % (totalCost))

# print the duration of the route 
totalDuration = 0
rDuration = [[3.8580611111111107, 4.801861111111111],[3.3397555555555556, 3.6825000000000006],[1.6580527777777778, 3.37925, 3.534922222222222, 3.816902777777778, 4.066802777777778, 3.3165916666666666, 3.6351111111111107],[1.9218722222222224, 3.599986111111111]]
for i in range(len(rDuration)):
    for j in range(len(rDuration[i])):
        totalDuration += rDuration[i][j]
print("Saturday total duration : %.2f hours" % (totalDuration))

m

Saturday total cost : $10081.06
Saturday total duration : 44.61 hours
